## Trafic data

> This <span style="color:MediumSeaGreen;">comptages-routiers - Toulouse Métropole, 2019-03-28</span> database is made available under the Open Database License: http://opendatacommons.org/licenses/odbl/1.0/. Any rights in individual contents of the database are licensed under the Database Contents License: http://opendatacommons.org/licenses/dbcl/1.0/

## 1. Reading data

In [1]:
import pandas as pd

In [2]:
urlAPI = "https://data.toulouse-metropole.fr/api/v2/catalog/datasets/comptages-routiers/exports/csv?rows=-1&timezone=UTC&delimiter=%3B"
rawdata = pd.read_csv(urlAPI, sep=';')

In [3]:
trafic = rawdata.copy()
trafic.head()

street                           motdir     commune  code_insee  \
0  CHE DE BESSAYRE       BESSAYRE (CHE DE BESSAYRE)     St-Jean       31488   
1    RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE    Toulouse       31555   
2    RUE DE MAURYS           MAURYS (RUE DE MAURYS)  Gratentour       31230   
3    RUE DU TASCAS           TASCAS (RUE DU TASCAS)  Gratentour       31230   
4  RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)    Toulouse       31555   

  date_comptage   annee                         section     sens_de_comptage  \
0    2014-02-08  2014.0          ENTRE VALLON ET MERMOZ  VERS CH DE MONTRABE   
1    2014-05-14  2014.0           ENTRE ORIENT ET LAFON           VERS LAFON   
2    2014-04-21  2014.0  ENTRE TASCAS ET AV DE TOULOUSE      VERS GRATENTOUR   
3    2014-04-24  2014.0        ENTRE MAURYS ET PRUNIERS      VERS PECHBONIEU   
4    2014-04-08  2014.0     ENTRE SURCOUF ET FRATERNITE         VERS SURCOUF   

  voie_en_sens_unique type  moyenne_jours_ouvres_par_semaine  
0                 NaN   TV                            4010.0  
1                 oui   TV                            7036.0  
2                 NaN   TV                            2309.0  
3                 NaN   TV                            3104.0  
4                 NaN   TV                            4669.0

## 2. Cleaning data

Since this dataset is natively french, let's first translate and clean the columns names.  
* `motdir`                           ⇔ direction/main word 
* `commune`                          ⇔ township
* `code_insee`                       ⇔ Insee township postal code *([Insee](https://en.wikipedia.org/wiki/Institut_national_de_la_statistique_et_des_%C3%A9tudes_%C3%A9conomiques) is a french official public statistical institute)*
* `date_comptage`                    ⇔ count date
* `annee`                            ⇔ year
* `section`                          ⇔ section *(used as further street location indications where measurements took place)*
* `sens_de_comptage`                 ⇔ counting direction
* `voie_en_sens_unique`              ⇔ one-way street
* `type`                             ⇔ type *(? I don't know the meaning of this variable or the interpretation of its values but it doesn't matter since the feature seems useless)*
* `moyenne_jours_ouvres_par_semaine` ⇔ average per week days *(Monday to Friday)*


In [4]:
trafic.columns = ['street', 'dir_word', 'township', 'insee_postal_code', 'count_date', 'year', 'section', 'count_direction', 'one_way', 'type', 'avg_perweekday']

Let's also fix the features types.

In [5]:
trafic['insee_postal_code'] = trafic['insee_postal_code'].astype(str)

trafic['count_date'] = pd.to_datetime(trafic['count_date'], format='%Y-%m-%d')

trafic['year'] = pd.to_datetime(trafic['year'], format='%Y')

filt = trafic['one_way'] == 'oui'
trafic['one_way'] = filt

trafic.drop('type', axis=1, inplace=True)

In [6]:
trafic.head()

street                         dir_word    township  \
0  CHE DE BESSAYRE       BESSAYRE (CHE DE BESSAYRE)     St-Jean   
1    RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE    Toulouse   
2    RUE DE MAURYS           MAURYS (RUE DE MAURYS)  Gratentour   
3    RUE DU TASCAS           TASCAS (RUE DU TASCAS)  Gratentour   
4  RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)    Toulouse   

  insee_postal_code count_date       year                         section  \
0             31488 2014-02-08 2014-01-01          ENTRE VALLON ET MERMOZ   
1             31555 2014-05-14 2014-01-01           ENTRE ORIENT ET LAFON   
2             31230 2014-04-21 2014-01-01  ENTRE TASCAS ET AV DE TOULOUSE   
3             31230 2014-04-24 2014-01-01        ENTRE MAURYS ET PRUNIERS   
4             31555 2014-04-08 2014-01-01     ENTRE SURCOUF ET FRATERNITE   

       count_direction  one_way  avg_perweekday  
0  VERS CH DE MONTRABE    False          4010.0  
1           VERS LAFON     True          7036.0  
2      VERS GRATENTOUR    False          2309.0  
3      VERS PECHBONIEU    False          3104.0  
4         VERS SURCOUF    False          4669.0

In [7]:
trafic.shape

(3735, 10)

In [8]:
filtre = trafic['township'] == 'Toulouse'
tls_trafic = trafic[filtre]

In [9]:
addresses = tls_trafic.loc[0:5,'street'] + ', Toulouse ' + tls_trafic.loc[0:5,'insee_postal_code']

In [11]:
from geopy.geocoders import Nominatim

latitudes = list()
longitudes = list()

for i, address in enumerate(addresses):
    geolocator = Nominatim(user_agent="foursquare_agent") # arbitrary name
    location = geolocator.geocode(address)
    latitudes.append(location.latitude)
    longitudes.append(location.longitude)

In [12]:
print(latitudes)
print(longitudes)

[43.6097203, 43.6140106, 43.6140602]
[1.4493484, 1.4760114, 1.4261224]


In [14]:
import geocoder

latitudes = list()
longitudes = list()

for address in addresses:
    g = geocoder.arcgis('Mountain View, CA')
    latitudes.append(g.latlng[0])
    longitudes.append(g.latlng[1])

In [15]:
print(latitudes)
print(longitudes)

[37.389670000000024, 37.389670000000024, 37.389670000000024]
[-122.08159999999998, -122.08159999999998, -122.08159999999998]


# Geographic data

## 1. Reading data

In [16]:
import requests

# from DATA.toulouse-metropole
url_pstCode = "https://data.toulouse-metropole.fr/explore/dataset/codes-postaux-de-toulouse/download/?format=geojson&timezone=Europe/Berlin&lang=fr"

# from LA POSTE
url_code = "https://datanova.laposte.fr/explore/dataset/laposte_hexasmal/download/?format=geojson&timezone=Europe/Berlin&lang=fr"

In [17]:
import geopandas

tls_pstCode = geopandas.read_file(url_pstCode)
fr_allCode = geopandas.read_file(url_code)

In [18]:
tls_pstCode.head()

code_postal  id_code_postal  \
0       31000               1   
1       31840              21   
2       31400              12   
3       31130               3   
4       31140               4   

                                            geometry  
0  POLYGON ((1.41199 43.60893, 1.41336 43.60960, ...  
1  POLYGON ((1.29626 43.69456, 1.29637 43.69458, ...  
2  POLYGON ((1.50411 43.55588, 1.50410 43.55588, ...  
3  POLYGON ((1.48992 43.63296, 1.49053 43.63312, ...  
4  POLYGON ((1.46224 43.68394, 1.46224 43.68394, ...

In [19]:
fr_allCode.head()

code_commune_insee libelle_d_acheminement      nom_de_la_commune  \
0              25628  VILLERS SOUS MONTROND  VILLERS SOUS MONTROND   
1              26001       SOLAURE EN DIOIS       SOLAURE EN DIOIS   
2              26001       SOLAURE EN DIOIS       SOLAURE EN DIOIS   
3              26006                  ALLEX                  ALLEX   
4              26013                ARPAVON                ARPAVON   

  code_postal           ligne_5                  geometry  
0       25620              None  POINT (6.08965 47.14537)  
1       26150      AIX EN DIOIS  POINT (5.38335 44.70241)  
2       26150  MOLIERES GLANDAZ  POINT (5.38335 44.70241)  
3       26400              None  POINT (4.91520 44.76655)  
4       26110              None  POINT (5.27351 44.37091)

In [20]:
trafic['insee_postal_code'].isin(tls_pstCode['code_postal']).value_counts()

False    3655
True       80
Name: insee_postal_code, dtype: int64

In [21]:
trafic['insee_postal_code'].isin(fr_allCode['code_commune_insee']).value_counts()

True    3735
Name: insee_postal_code, dtype: int64

In [22]:
geo_pstCode = tls_pstCode.join(fr_allCode.set_index('code_postal'), rsuffix='_location', on="code_postal")
geo_pstCode.head()

code_postal  id_code_postal  \
0       31000               1   
1       31840              21   
1       31840              21   
2       31400              12   
3       31130               3   

                                            geometry code_commune_insee  \
0  POLYGON ((1.41199 43.60893, 1.41336 43.60960, ...              31555   
1  POLYGON ((1.29626 43.69456, 1.29637 43.69458, ...              31032   
1  POLYGON ((1.29626 43.69456, 1.29637 43.69458, ...              31541   
2  POLYGON ((1.50411 43.55588, 1.50410 43.55588, ...              31555   
3  POLYGON ((1.48992 43.63296, 1.49053 43.63312, ...              31044   

  libelle_d_acheminement nom_de_la_commune ligne_5         geometry_location  
0               TOULOUSE          TOULOUSE    None  POINT (1.43167 43.59638)  
1               AUSSONNE          AUSSONNE    None  POINT (1.32887 43.68360)  
1                  SEILH             SEILH    None  POINT (1.35675 43.69010)  
2               TOULOUSE          TOULOUSE    None  POINT (1.43167 43.59638)  
3                  BALMA             BALMA    None  POINT (1.50459 43.61153)

## 2. Cleaning data

In [23]:
geo_pstCode['center_latitude'] = geo_pstCode['geometry'].centroid.bounds['miny']
geo_pstCode['center_longitude'] = geo_pstCode['geometry'].centroid.bounds['minx']

# Remove useless features
geo_pstCode.drop(columns=['id_code_postal',
                          'libelle_d_acheminement',
                          'nom_de_la_commune',
                          'ligne_5',
                          'geometry_location',], inplace=True)

# Rename remaining columns
geo_pstCode.columns = ['postal_code', 'geometry', 'insee_postal_code', 'center_latitude', 'center_longitude']
geo_pstCode.head()

<ipython-input-23-d3795b55ca9c>:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  geo_pstCode['center_latitude'] = geo_pstCode['geometry'].centroid.bounds['miny']
<ipython-input-23-d3795b55ca9c>:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  geo_pstCode['center_longitude'] = geo_pstCode['geometry'].centroid.bounds['minx']


postal_code                                           geometry  \
0       31000  POLYGON ((1.41199 43.60893, 1.41336 43.60960, ...   
1       31840  POLYGON ((1.29626 43.69456, 1.29637 43.69458, ...   
1       31840  POLYGON ((1.29626 43.69456, 1.29637 43.69458, ...   
2       31400  POLYGON ((1.50411 43.55588, 1.50410 43.55588, ...   
3       31130  POLYGON ((1.48992 43.63296, 1.49053 43.63312, ...   

  insee_postal_code  center_latitude  center_longitude  
0             31555        43.605317          1.440060  
1             31032        43.685717          1.337217  
1             31541        43.685717          1.337217  
2             31555        43.568608          1.465193  
3             31044        43.604213          1.528549

## 3. Mapping data

In [24]:
trafic = trafic.join(geo_pstCode.drop(columns=['geometry']).set_index('insee_postal_code'), on="insee_postal_code")
trafic.head()

street                         dir_word  township  \
0  CHE DE BESSAYRE       BESSAYRE (CHE DE BESSAYRE)   St-Jean   
1    RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1    RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1    RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1    RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   

  insee_postal_code count_date       year                 section  \
0             31488 2014-02-08 2014-01-01  ENTRE VALLON ET MERMOZ   
1             31555 2014-05-14 2014-01-01   ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01   ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01   ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01   ENTRE ORIENT ET LAFON   

       count_direction  one_way  avg_perweekday postal_code  center_latitude  \
0  VERS CH DE MONTRABE    False          4010.0       31240        43.658261   
1           VERS LAFON     True          7036.0       31000        43.605317   
1           VERS LAFON     True          7036.0       31400        43.568608   
1           VERS LAFON     True          7036.0       31100        43.567874   
1           VERS LAFON     True          7036.0       31300        43.605006   

   center_longitude  
0          1.491755  
1          1.440060  
1          1.465193  
1          1.398301  
1          1.391986

In [25]:
filt = trafic['township'] == 'Toulouse'
trafic_dwntwn = trafic[filt]
trafic_dwntwn.head()

street                         dir_word  township insee_postal_code  \
1  RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse             31555   
1  RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse             31555   
1  RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse             31555   
1  RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse             31555   
1  RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse             31555   

  count_date       year                section count_direction  one_way  \
1 2014-05-14 2014-01-01  ENTRE ORIENT ET LAFON      VERS LAFON     True   
1 2014-05-14 2014-01-01  ENTRE ORIENT ET LAFON      VERS LAFON     True   
1 2014-05-14 2014-01-01  ENTRE ORIENT ET LAFON      VERS LAFON     True   
1 2014-05-14 2014-01-01  ENTRE ORIENT ET LAFON      VERS LAFON     True   
1 2014-05-14 2014-01-01  ENTRE ORIENT ET LAFON      VERS LAFON     True   

   avg_perweekday postal_code  center_latitude  center_longitude  
1          7036.0       31000        43.605317          1.440060  
1          7036.0       31400        43.568608          1.465193  
1          7036.0       31100        43.567874          1.398301  
1          7036.0       31300        43.605006          1.391986  
1          7036.0       31200        43.637970          1.438258

### Simple map of postal codes

In [26]:
import folium
import geocoder

In [29]:
g = geocoder.arcgis('Toulouse, France')
lat_lng_coords = g.latlng
lat_tls = lat_lng_coords[0]
lng_tls = lat_lng_coords[1]

# create map of Toulouse using latitude and longitude values
toulouse_map = folium.Map(location=[lat_tls, lng_tls], zoom_start=11)

# generate choropleth map using the total immigration of each country to Canada from 1980 to 2013
folium.GeoJson(
    tls_pstCode['geometry'],
    style_function=lambda feature: {
        'fillColor': '#ffff00',
        'color': 'black',
        'weight': 2,
        'dashArray': '2, 5'
    }
).add_to(toulouse_map)

toulouse_map

### Post Codes Choropleth Map

In [30]:
trafic_grp = trafic_dwntwn.groupby(['postal_code'])
test = trafic_dwntwn.groupby(['postal_code'], as_index=False).mean()

In [31]:
trafic_grp.head()

street                         dir_word  township  \
1        RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1        RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1        RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1        RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1        RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
1        RUE DE BAYARD  BAYARD (RUE DE BAYARD)_TOULOUSE  Toulouse   
4      RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)  Toulouse   
4      RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)  Toulouse   
4      RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)  Toulouse   
4      RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)  Toulouse   
4      RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)  Toulouse   
4      RUE LOUIS PLANA          PLANA (RUE LOUIS PLANA)  Toulouse   
5   RUE CHARLES GOUNOD      GOUNOD (RUE CHARLES GOUNOD)  Toulouse   
5   RUE CHARLES GOUNOD      GOUNOD (RUE CHARLES GOUNOD)  Toulouse   
5   RUE CHARLES GOUNOD      GOUNOD (RUE CHARLES GOUNOD)  Toulouse   
5   RUE CHARLES GOUNOD      GOUNOD (RUE CHARLES GOUNOD)  Toulouse   
5   RUE CHARLES GOUNOD      GOUNOD (RUE CHARLES GOUNOD)  Toulouse   
5   RUE CHARLES GOUNOD      GOUNOD (RUE CHARLES GOUNOD)  Toulouse   
7  RUE EMILE LECRIVAIN  LECRIVAIN (RUE EMILE LECRIVAIN)  Toulouse   
7  RUE EMILE LECRIVAIN  LECRIVAIN (RUE EMILE LECRIVAIN)  Toulouse   
7  RUE EMILE LECRIVAIN  LECRIVAIN (RUE EMILE LECRIVAIN)  Toulouse   
7  RUE EMILE LECRIVAIN  LECRIVAIN (RUE EMILE LECRIVAIN)  Toulouse   
7  RUE EMILE LECRIVAIN  LECRIVAIN (RUE EMILE LECRIVAIN)  Toulouse   
7  RUE EMILE LECRIVAIN  LECRIVAIN (RUE EMILE LECRIVAIN)  Toulouse   
9           AV CRAMPEL             CRAMPEL (AV CRAMPEL)  Toulouse   
9           AV CRAMPEL             CRAMPEL (AV CRAMPEL)  Toulouse   
9           AV CRAMPEL             CRAMPEL (AV CRAMPEL)  Toulouse   
9           AV CRAMPEL             CRAMPEL (AV CRAMPEL)  Toulouse   
9           AV CRAMPEL             CRAMPEL (AV CRAMPEL)  Toulouse   
9           AV CRAMPEL             CRAMPEL (AV CRAMPEL)  Toulouse   

  insee_postal_code count_date       year                      section  \
1             31555 2014-05-14 2014-01-01        ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01        ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01        ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01        ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01        ENTRE ORIENT ET LAFON   
1             31555 2014-05-14 2014-01-01        ENTRE ORIENT ET LAFON   
4             31555 2014-04-08 2014-01-01  ENTRE SURCOUF ET FRATERNITE   
4             31555 2014-04-08 2014-01-01  ENTRE SURCOUF ET FRATERNITE   
4             31555 2014-04-08 2014-01-01  ENTRE SURCOUF ET FRATERNITE   
4             31555 2014-04-08 2014-01-01  ENTRE SURCOUF ET FRATERNITE   
4             31555 2014-04-08 2014-01-01  ENTRE SURCOUF ET FRATERNITE   
4             31555 2014-04-08 2014-01-01  ENTRE SURCOUF ET FRATERNITE   
5             31555 2014-03-20 2014-01-01   ENTRE BAUDELAIRE ET KRUGER   
5             31555 2014-03-20 2014-01-01   ENTRE BAUDELAIRE ET KRUGER   
5             31555 2014-03-20 2014-01-01   ENTRE BAUDELAIRE ET KRUGER   
5             31555 2014-03-20 2014-01-01   ENTRE BAUDELAIRE ET KRUGER   
5             31555 2014-03-20 2014-01-01   ENTRE BAUDELAIRE ET KRUGER   
5             31555 2014-03-20 2014-01-01   ENTRE BAUDELAIRE ET KRUGER   
7             31555 2014-05-17 2014-01-01   ENTRE CARROSSE ET COLLENOT   
7             31555 2014-05-17 2014-01-01   ENTRE CARROSSE ET COLLENOT   
7             31555 2014-05-17 2014-01-01   ENTRE CARROSSE ET COLLENOT   
7             31555 2014-05-17 2014-01-01   ENTRE CARROSSE ET COLLENOT   
7             31555 2014-05-17 2014-01-01   ENTRE CARROSSE ET COLLENOT   
7             31555 2014-05-17 2014-01-01   ENTRE CARROSSE ET COLLENOT   
9             31555 2014-0

In [34]:
toulouse_map = folium.Map(location=[lat_tls, lng_tls], zoom_start=11)

toulouse_map.choropleth(
    geo_data=tls_pstCode['geometry'],
    data=test,
    columns=['postal_code', 'avg_perweekday'],
    fill_color='YlOrRd',
    key_on='properties.code_postal',
    fill_opacity=0.3, 
    line_opacity=0.3,
    legend_name='Immigration to Canada',
    highlight=True
)

for lat, lng in zip(geo_pstCode['center_latitude'], geo_pstCode['center_longitude']):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(toulouse_map)
    

toulouse_map

# Foursquare venues

In [35]:
# IDs for "coursera-capstone-project" app
CLIENT_ID = '3HKNONV5WQ0YZJUOEYSE0221FMCZQDZHKNQ0W4ZG1P5XW2KW'
CLIENT_SECRET = '0TIKF1OFORWQTIPFVVLMGHHQST3LPPTBLMKXATPVIUPFJXUU'
VERSION = '20180323'
LIMIT = 300
radius = 3000

In [38]:
items = list()

for latitude, longitude in zip(geo_pstCode['center_latitude'], geo_pstCode['center_longitude']):
    
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT)

    results = requests.get(url).json()

    items.extend(results['response']['groups'][0]['items'])

In [53]:
import json, requests
url = 'https://api.foursquare.com/v2/venues/explore'

params = dict(
client_id='3HKNONV5WQ0YZJUOEYSE0221FMCZQDZHKNQ0W4ZG1P5XW2KW',
client_secret='0TIKF1OFORWQTIPFVVLMGHHQST3LPPTBLMKXATPVIUPFJXUU',
v='20180323',
ll=str(lat_tls) + ',' + str(lng_tls),
query='loisirs',
limit=300,
locale='fr',
radius=3000
)
resp = requests.get(url=url, params=params)
data = json.loads(resp.text)



In [54]:
items = data['response']['groups'][0]['items']

In [56]:
from pandas import json_normalize

dataframe = json_normalize(items) # flatten JSON

filtered_columns = ['venue.name', 'venue.categories'] + [col for col in dataframe.columns if col.startswith('venue.location.')] + ['venue.id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['venue.categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean columns
dataframe_filtered.columns = [col.split('.')[-1] for col in dataframe_filtered.columns]

dataframe_filtered

name           categories  \
0                          Théâtre du Capitole                Opéra   
1        Hôtel de Ville de Toulouse (Capitole)       Hôtel de ville   
2                               Gaumont Wilson           Multiplexe   
3                          Musée des Augustins          Musée d'art   
4   Théâtre National de Toulouse Midi-Pyrénées              Théâtre   
5                               Théâtre Les 3T   Salle de spectacle   
6                             Halle aux Grains     Salle de concert   
7               Parc de la Prairie des Filtres                 Parc   
8                         Jardin du Grand Rond               Jardin   
9                                Cinéma Utopia   Cinéma indépendant   
10                          Muséum de Toulouse   Musée des sciences   
11                                    Rio Loco     Salle de concert   
12                      La Comédie de Toulouse   Salle de spectacle   
13          Les Abattoirs - FRAC Midi-Pyrénées          Musée d'art   
14                                 Palais Niel       Base militaire   
15                           Fondation Bemberg          Musée d'art   
16                               Château d'eau        Galerie d'art   
17                           Palais des sports  Stade de basketball   
18                           Stadium Municipal    Stade de football   
19                         Musée Saint-Raymond     Musée d'histoire   
20                 La Cinémathèque de Toulouse               Cinéma   
21                Église Notre Dame la Dalbade               Église   
22                                Le Seventies      Café des sports   
23                                  Cinéma ABC   Cinéma indépendant   
24                                   La Dynano     Salle de concert   
25                       Square Edouard Privat                 Parc   
26        Auditorium Saint Pierre Des Cuisines     Salle de concert   
27           Église Saint-Pierre des Chartreux      Site historique   
28                          Galerie Des Carmes        Galerie d'art   
29                                 Grande Roue   Parc d'attractions   
30                       Siestes Electroniques     Salle de concert   
31                         Centre James Carlès       Salle de danse   
32                                   jeux geek       Salle d'arcade   
33                Ecole De Danse Gilles Vezien       Salle de danse   
34                               Stade Arnaune                Stade   
35                                    Le bijou     Salle de concert   
36                          Parc Des Argoulets                 Parc   

                               address        lat       lng  \
0                    Place du Capitole  43.604130  1.444332   
1                    Place du Capitole  43.604523  1.444179   
2   3 place du Président Thomas Wilson  43.604251  1.448624   
3                       21 Rue de Metz  43.601170  1.446397   
4                       1-3 rue Labeda  43.604209  1.449935   
5                  40 rue Gabriel Péri  43.606037  1.455694   
6                          Place Dupuy  43.600015  1.454166   
7                         Cours Dillon  43.595638  1.436977   
8                    Square Boulingrin  43.595987  1.452373   
9                      24 Rue Montardy  43.604095  1.446715   
10               35 Allée Jules Guesde  43.593853  1.449469   
11                                 NaN  43.596345  1.436907   
12                   Rue Saint-Germier  43.611599  1.441049   
13          76 Allées Charles de Fitte  43.600773  1.429066   
14        Rue Montoulieu Saint-Jacques  43.597029  1.451311   
15                     Hôtel d'Assézat  43.600408  1.441880   
16                     1 Place Laganne  43.598832  1.436718   
17                                 NaN  43.612388  1.435369   
18              1 allée Gabriel Biénès  43.583251  1.434043   
19                  Place Saint-Sernin  43.607728  1.441115   
20                  

In [65]:
categorie_labels = {
    # Watch a show
    "spectacle": ["Opéra", "Théâtre", "Salle de spectacle"],
    "cinema": ["Multiplexe", "Cinéma indépendant", "Cinéma"],
    "music": ["Salle de concert"],

    # Visit a place
    "monument": ["Hôtel de ville", "Base militaire", "Église", "Site historique"],

    # Play
    "sport": ["Stade de basketball", "Stade de football", "Café des sports", "Salle de danse"],
    "game": ["Salle d'arcade", "Parc d'attractions"],

    # Interact with culture
    "exposition": ["Musée d'art", "Musée des sciences", "Galerie d'art", "Musée d'histoire"],

    # Enjoy green
    "parc": ["Parc", "Jardin"]
}

In [99]:
for i, cat_val in enumerate(categorie_labels.values()):
    filt = list(map(lambda cat_venu: cat_venu in cat_val,
                    dataframe_filtered['categories']))
    dataframe_filtered.loc[filt,'categories'] = list(categorie_labels.keys())[i]

In [101]:
dataframe_filtered.head()

name  categories  \
0                         Théâtre du Capitole   spectacle   
1       Hôtel de Ville de Toulouse (Capitole)    monument   
2                              Gaumont Wilson      cinema   
3                         Musée des Augustins  exposition   
4  Théâtre National de Toulouse Midi-Pyrénées   spectacle   

                              address        lat       lng  \
0                   Place du Capitole  43.604130  1.444332   
1                   Place du Capitole  43.604523  1.444179   
2  3 place du Président Thomas Wilson  43.604251  1.448624   
3                      21 Rue de Metz  43.601170  1.446397   
4                      1-3 rue Labeda  43.604209  1.449935   

                                      labeledLatLngs  distance postalCode  cc  \
0  [{'label': 'display', 'lat': 43.60412979544746...       392      31000  FR   
1  [{'label': 'display', 'lat': 43.60452250885116...       385      31000  FR   
2  [{'label': 'display', 'lat': 43.60425144568281...       171      31000  FR   
3  [{'label': 'display', 'lat': 43.6011697382502,...       544      31000  FR   
4  [{'label': 'display', 'lat': 43.60420866143894...       205      31000  FR   

       city          state country  \
0  Toulouse  Midi-Pyrénées  France   
1  Toulouse  Midi-Pyrénées  France   
2  Toulouse  Midi-Pyrénées  France   
3  Toulouse  Midi-Pyrénées  France   
4  Toulouse  Midi-Pyrénées  France   

                                    formattedAddress    crossStreet  \
0        [Place du Capitole, 31000 Toulouse, France]            NaN   
1  [Place du Capitole (Rue Lafayette), 31000 Toul...  Rue Lafayette   
2  [3 place du Président Thomas Wilson, 31000 Tou...            NaN   
3           [21 Rue de Metz, 31000 Toulouse, France]            NaN   
4           [1-3 rue Labeda, 31000 Toulouse, France]            NaN   

                         id  
0  4c84b599d92ea093f9785f72  
1  4c03b2459a7920a19230d079  
2  4b8a8935f964a520297132e3  
3  4b96adcbf964a52077dd34e3  
4  4c4c90cef7cc1b8df7a98041

In [106]:
toulouse_map = folium.Map(location=[lat_tls, lng_tls], zoom_start=14)

toulouse_map.choropleth(
    geo_data=tls_pstCode['geometry'],
    data=test,
    columns=['postal_code', 'avg_perweekday'],
    fill_color='YlOrRd',
    key_on='properties.code_postal',
    fill_opacity=0.3, 
    line_opacity=0.3,
    legend_name='Immigration to Canada',
    highlight=True
)

for lat, lng, name, cat in zip(dataframe_filtered['lat'], dataframe_filtered['lng'], dataframe_filtered['name'], dataframe_filtered['categories']):
    label = '{}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(toulouse_map)
    
toulouse_map